# Multi-dimer NF-κB model

The below code will create the multi-dimer NF-κB model as parameterised in Mitchell et al. Science Signalling (2023) and run canonical pathway activation.

Make sure you have a julia kernel selected that has many threads. Here is how many threads you have available:

In [1]:
import Base.Threads
Threads.nthreads()

12

In [2]:
#packages we need
using DifferentialEquations
using Plots 
using CSV
using Distributions
using Random
using DataFrames
using JLD2
using FileIO
using StatsPlots
using Plots.PlotMeasures
using Statistics

plotly()

#if necessary:
#include(fixSpecies.jl)

┌ Warning: PlotlyBase 0.5.4 is not compatible with this version of Plots. The declared compatibility is 0.7.
└ @ Plots /home/simon/.julia/packages/Plots/yJrrq/src/Plots.jl:22


Plots.PlotlyBackend()

In [3]:
using Pkg
Pkg.status()

      Status `~/.julia/environments/v1.6/Project.toml`
  [fbb218c0] BSON v0.3.6
  [336ed68f] CSV v0.10.8
  [a93c6f00] DataFrames v0.22.7
  [2b5f629d] DiffEqBase v6.84.0
  [0c46a032] DifferentialEquations v6.20.0
  [31c24e10] Distributions v0.25.45
  [5789e2e9] FileIO v1.16.0
  [6a86dc24] FiniteDiff v2.17.0
  [28b8d3ca] GR v0.64.4
  [09f84164] HypothesisTests v0.10.11
  [7073ff75] IJulia v1.23.3 `https://github.com/JuliaLang/IJulia.jl.git#master`
  [033835bb] JLD2 v0.4.3
  [b964fa9f] LaTeXStrings v1.3.0
  [b4fcebef] Lasso v0.6.2
  [21d151f5] LassoPlot v1.1.1
  [1dea7af3] OrdinaryDiffEq v5.71.2
  [69de0a69] Parsers v2.2.4
  [58dd65bb] Plotly v0.3.0
  [a03496cd] PlotlyBase v0.5.4
  [f0f68f2c] PlotlyJS v0.14.1
  [91a5bcdd] Plots v1.32.0
  [438e738f] PyCall v1.94.1
  [d330b81b] PyPlot v2.11.0
  [1a8c2f83] Query v1.0.0
  [102930c3] SmoothingSplines v0.3.1
  [f3b207a7] StatsPlots v0.14.34
  [c3572dad] Sundials v4.11.4
  [bd369af6] Tables v1.10.0
  [a759f4b9] TimerOutputs v0.5.22
  [0f1e0344] 

In [4]:
first_cell=1
last_cell=25

#set up where CSV2Julia is
#from: https://github.com/SiFTW/CSV2JuliaDiffEq
locationOfCSV2Julia="CSV2Julia/csv2model-multiscale.py"

#identify the three CSV sheets that describe the model
reactionsFile="moduleDefinitionFiles/updated_NFkB_reactions.csv"
parametersFile="moduleDefinitionFiles/parameters.csv"
rateLawsFile="moduleDefinitionFiles/rateLaws.csv"
generatedCSVLocation="generatedCSVs/"
distributedModelFilesLocation="distributedModelFiles/"


mkpath(generatedCSVLocation)
mkpath(distributedModelFilesLocation)

colorArray=palette(:seaborn_colorblind)

totalIKK=140
total_WT_IKK=totalIKK*1.0
basalIKK=totalIKK/100
IKKMultiplier=1
maxTimeSS=100000.0
maxTimeTC=60*8
preCV=0.11;
#preCV=0.0

In [5]:
function ikkDefault(t,maxTime)
    #explicitely defined input
    IKKparamVals=[0,85,100,85,45,30,25,23,18,15,12,10,10]./100
    paramTime=[0,5,10,15,18,20,300,400,450,480,500,520,max(maxTime,2880)]
    #get the value after the current time point
    indexGTTime=min(searchsortedfirst(paramTime,t),length(paramTime))
    #get the one before
    indexLTTime=max(1,indexGTTime-1)
    timeGTt=paramTime[indexGTTime]
    timeLTt=paramTime[indexLTTime]
    valGTt=IKKparamVals[indexGTTime]
    valLTt=IKKparamVals[indexLTTime]
    timeDiff=timeGTt-timeLTt
    #if the time before and time after are different do a basic linear interpolation between the two.
    if timeDiff>0
        valDiff=valGTt-valLTt
        gradient=valDiff/timeDiff
        timeStep=t-timeLTt
        return valLTt+(gradient*timeStep)
    else
        return valLTt
    end
end

function NIKDefault(t,maxTime)
    #explicitely defined input
    NIKparamVals=[1,50,100,180,200,100,50]./100
    paramTime=[0,60,120,300,400,800,max(maxTime,2880)]
    #get the value after the current time point
    indexGTTime=min(searchsortedfirst(paramTime,t),length(paramTime))
    #get the one before
    indexLTTime=max(1,indexGTTime-1)
    timeGTt=paramTime[indexGTTime]
    timeLTt=paramTime[indexLTTime]
    valGTt=NIKparamVals[indexGTTime]
    valLTt=NIKparamVals[indexLTTime]
    timeDiff=timeGTt-timeLTt
    #if the time before and time after are different do a basic linear interpolation between the two.
    if timeDiff>0
        valDiff=valGTt-valLTt
        gradient=valDiff/timeDiff
        timeStep=t-timeLTt
        return valLTt+(gradient*timeStep)
    else
        return valLTt
    end
end

#the IKK function is just maps to basal IKK during SS and basal+the IKK curve during the time course.
ikkSS=t->basalIKK
ikkTC=t->basalIKK+(ikkDefault(t, maxTimeTC)*IKKMultiplier*totalIKK);
ikkTCWT=t->basalIKK+(ikkDefault(t, maxTimeTC)*IKKMultiplier*total_WT_IKK);
ikkCurveForLine=[ikkTCWT]
ikkFunc=ikkTCWT
NIKFuncSS=t->1
NIKFuncTC=t->0
ikkSSHigh=t->basalIKKHigh

p=plot([1:1:maxTimeTC],ikkTC.(1:1:maxTimeTC),label="smooth fit",title="input curve");
xlabel!("time (h)")
ylabel!("active IKK")

The below code first creates the ODE file.

In [6]:
parametersDF = DataFrame(CSV.File(parametersFile,types=Dict(:parameter=>String, :value=>String, :distribute=>Int64)))
originalParams=deepcopy(parametersDF)

thisModelName="odeModel.jl"
thisParamFile=parametersFile
arguments=[reactionsFile, thisParamFile, rateLawsFile,thisModelName]
cmd=`python3 $locationOfCSV2Julia $arguments param`

#lets run csv2julia (requires python to be installed)
run(cmd)

include(thisModelName)
mv(thisModelName,"distributedModelFiles/"*thisModelName, force=true)
println("Model generated for all conditions")

param
Running CSV2JuliaDiffEq with parameters dynamically determined by a variable, re-run with the 5th argument set to 'scan' or 'inline'
Opening moduleDefinitionFiles/rateLaws.csv as rate law file
Opening moduleDefinitionFiles/parameters.csv as parameters file
Opening moduleDefinitionFiles/updated_NFkB_reactions.csv as reactions file
Model generated for all conditions


The below function will run the number of cells you specify, with the conditions you specify and the input curves specified. It will use multiple threads to do so and save the results in a different folder for each condition.

In [7]:
include("variableNames.jl")

101-element Vector{String}:
 "RelA"
 "p50"
 "RelAp50"
 "RelAn"
 "p50n"
 "RelAnp50n"
 "p52"
 "RelAp52"
 "p52n"
 "RelAnp52n"
 "RelB"
 "RelBp52"
 "RelBn"
 ⋮
 "tcRel"
 "p100"
 "p100n"
 "NIK"
 "p100NIK"
 "IkBdNIK"
 "RelAp50IkBdNIK"
 "RelBp50IkBdNIK"
 "RelBp52IkBdNIK"
 "cRelp50IkBdNIK"
 "cRelp52IkBdNIK"
 "RelAp52IkBdNIK"

In [8]:
function runSimulationNew(first_cell, last_cell, conditions,folder,IKKSSArray,IKKTCArray,NIKSSArray,NIKTCArray)
    mkpath(folder)
    #now lets loop through and solve the cell
    TCLength=1000*60
    maximumAttemptsAtSS=10
    include("variableNames.jl")
    include("scanIncludes.jl")
    originalParams=copy(paramVals)
    ikkIndex=findfirst(x -> x=="ikk1_ikkactivity", parameterNameList)
    NIKIndex=findfirst(x -> x=="nik_deg_mod", parameterNameList)
    
    thisDist=TruncatedNormal(1.0, preCV,0,Inf)


    Random.seed!(123)    


    allParams=[]
    allParams=Array{Any}(undef, size(parametersDF,1), last_cell)
    for cellIndex in first_cell:last_cell
        thisCellsParamVals=copy(originalParams)            

        for j in 1:size(parametersDF,1)
            if parametersDF[j,3]==1
                x = rand(thisDist, 1)
               thisCellsParamVals[j]=thisCellsParamVals[j].*x[1]
            end
        end
        #println(thisCellsParamVals)
        allParams[:,cellIndex]=thisCellsParamVals
    end
    df = DataFrame(allParams,:auto)
    #add the variable names and save to a file
    insertcols!(df, 1, :names=>parameterNameList)

    CSV.write(folder*"/allParams_runSimulationNew.csv",df);
    #println(size(allParams))
    #println(allParams[1])
    allParamsOriginal=copy(allParams)
    for condIndex in 1:length(conditions)
        allParams=copy(allParamsOriginal)
        thisCondition = conditions[condIndex]
        #TODO: consider making a condition scaling factor array here and just multiplying all prameters by it every time.
        
        println("Starting condition: "*thisCondition)
        odeName="odeModel"
        myFun=getfield(Main,Symbol(odeName))

        #define the function and the initial conditions
        f=ODEFunction(myFun,syms=Symbol.(syms))
        y0=zeros(length(syms))
    
        paramsListInThisCondition=paramsToChange[condIndex]
        modifyListInThisCondition=modifyAmount[condIndex]

        for thisParamIndex in 1:length(paramsListInThisCondition)
            thisParam=paramsListInThisCondition[thisParamIndex]
            thisParamsIndexInParamList=findfirst(x->x==thisParam,parameterNameList)
            allParams[thisParamsIndexInParamList,:]=allParams[thisParamsIndexInParamList,:].*modifyListInThisCondition[thisParamIndex]
        end  
        df = DataFrame(allParams,:auto)
        #add the variable names and save to a file
        insertcols!(df, 1, :names=>parameterNameList)
        CSV.write(folder*"/allParams_runSimulationNew_"*thisCondition*".csv",df);

        Threads.@threads for i in first_cell:last_cell
            #figure out the name of this cell's ode file
            
            #DISTRIBUTE PARAMS
            
            println("starting cell: "*string(i))
            thisCellsParamVals=copy(allParams[:,i])
            thisCellsParamVals[ikkIndex]=IKKSSArray[condIndex]
            thisCellsParamVals[NIKIndex]=NIKSSArray[condIndex]
            
      
    #     #now write this condition's CSV file to a folder of cells
    #     CSV.write(generatedCSVLocation*"/parameters_"*string(conditions[condIndex])*".csv", thisCondParamFile)

            prob=ODEProblem(f,y0,(0.0,maxTimeSS),thisCellsParamVals)

            solss=solve(prob,saveat=100.0,progress = true)
            println("Steady state found for cell: "*string(i))

            #dynamic phase, use SS solution as initial conditions
            y0=vec(convert(Array, solss[:,end]))
            y0[y0.<0].=0
            thisCellsParamVals[ikkIndex]=IKKTCArray[condIndex]
            thisCellsParamVals[NIKIndex]=NIKTCArray[condIndex]
            #CSV.write(generatedCSVLocation*"/parameters_"*string(conditions[condIndex])*"_cell_"*string(i)*".csv", DataFrame(thisCellsParamVals,:auto))
            try
                f=ODEFunction(myFun,syms=syms)
                prob=ODEProblem(f,y0,(0.0,maxTimeTC),thisCellsParamVals)
                println("Solving equations for dynamic time course for cell:"*string(i))
                sol=solve(prob, abstol=1e-5,reltol=1e-3, saveat=1.0)
                #save("outputs/sol_"*thisCondition*"_cell_"*string(i)*".jld2", "solution", sol)
                df = DataFrame(Float64.(sol),:auto)
                #add the variable names and save to a file
                insertcols!(df, 1, :names=>syms)
                #CSV.write("outputs/sol_"*thisCondition*"_cell_"*string(i)*".csv",Tables.columntable(df));
                CSV.write(folder*"/sol_"*thisCondition*"_cell_"*string(i)*".csv",df);
            catch e
                println("error:")
                println(e)
            end

        end
        println("all cells done in condition: "*thisCondition)

    end
end

runSimulationNew (generic function with 1 method)

The below code is used to plot some graphs. It will plot the species you specify and compare between each condition. It will plot both steady state values (as bar graphs on the left), and time courses (as line graphs on the right). IT will calculate the standard deviation and mean of each cell populationin each condition and show them as error regions.

In [9]:
function plotAllSpecies(speciesToPlot,conditionsToPlot,colorArray,first_cell,last_cell,folder,hoursToPlot,maxValOfYAxis)
    for species in speciesToPlot
        #thisPlot=plot(title=species)
#         thisPlotStd=plot(title=species*" avg")
#         boxPlotAll=plot(title=species*" ss")
#         BoxPlotAvg=plot(title=species*"avg ss")
        thisPlotStd=plot()
        boxPlotAll=plot()
        BoxPlotAvg=plot()
        conditionIndex=1
        meansOfAllConditions=zeros(1,length(conditionsToPlot))
        stdOfAllConditions=zeros(1,length(conditionsToPlot))
        lengthOfTC=0
        for condition in conditionsToPlot
            lengthOfTC=size(DataFrame(CSV.File(folder*"/sol_"*condition*"_cell_1.csv")),2)-1

            conditionArray=zeros(last_cell,lengthOfTC)
            conditionArrayNorm=zeros(last_cell,lengthOfTC)
            lineColor=colorArray[conditionIndex]
            virtExpFlag=false
            for i in first_cell:last_cell
                thisCellData=DataFrame(CSV.File(folder*"/sol_"*condition*"_cell_"*string(i)*".csv"))
                if !("names" in names(thisCellData))
                    insertcols!(thisCellData, 1, :names=>syms)
                end
                allNoneFloats=findall(eltype.(eachcol(thisCellData)).!=Float64)
                if length(allNoneFloats)>1
                    for index in allNoneFloats[2:end]
                        thisCellData[!,index]=parse.(Float64,thisCellData[:,index])
                    end
                end
                thisTC=zeros(1,size(thisCellData,2)-1)
                if endswith(species,"*")
                    virtExpFlag=true
                    speciesShort=species[1:end-1]
                    speciesIDs=intersect(findall( x ->occursin(speciesShort,x),syms),findall(x->!startswith(x,"t"),syms))
                    speciesNames=String.(syms[speciesIDs])
#                     println("For species: "*species*" printing: ")
#                     println(speciesNames)
                    for thisName in speciesNames
                        thisSpeciesTC=convert(Matrix, thisCellData[thisCellData[!,:names].==thisName,:])[2:end]
                        
                        thisTC=thisTC.+thisSpeciesTC'
                    end
                else
                    thisTC=convert(Matrix, thisCellData[thisCellData[!,:names].==species,:])[2:end]
                end
                conditionArray[i,:]=thisTC[1:lengthOfTC]
                conditionArrayNorm[i,:]=thisTC[1:lengthOfTC]./thisTC[1]


            end

            df = DataFrame(Float64.(conditionArray),:auto)
            #add the variable names and save to a file
            #CSV.write("outputs/sol_"*thisCondition*"_cell_"*string(i)*".csv",Tables.columntable(df));
            CSV.write("outputs/allTCs_"*species*"_cell.csv",df);

            
            meanOfConditionNorm=mean(conditionArrayNorm, dims=1)
            stdOfConditionNorm=std(conditionArrayNorm, dims=1)
            meanOfCondition=mean(conditionArray, dims=1)
            stdOfCondition=std(conditionArray, dims=1)
#             println(meanOfCondition)
#             println(stdOfCondition)
            plot!(thisPlotStd,meanOfConditionNorm',grid=false,color=lineColor,ribbon=stdOfConditionNorm',fillalpha=.5,label=condition,linewidth=5)

            meansOfAllConditions[conditionIndex]=meanOfCondition[1]
            stdOfAllConditions[conditionIndex]=stdOfCondition[1]

            conditionIndex+=1
        end
        conditionIndex=1
        #plot!(boxPlotAll,conditionsToPlot, meansOfAllConditions;, c=colorArray, yerr = stdOfAllConditions', label = "",xrotation = 90,seriestype = :scatter,fillcolor=:match)
        for condition in conditionsToPlot
            plot!(boxPlotAll,[conditionIndex], [meansOfAllConditions[conditionIndex]], c=colorArray[conditionIndex], yerr = stdOfAllConditions[conditionIndex],label = false,xrotation = 90,seriestype = :scatter,fillcolor=:match,markersize=7,markerstrokewidth=3)            
            conditionIndex+=1
        end
        plot!(boxPlotAll,xticks = (1:length(conditions), conditions),xlim=(0,length(conditionsToPlot)+1),dpi=300,size=(400,500),xtickfontsize=18,ytickfontsize=18,ylim=(0,maximum(meansOfAllConditions.+stdOfAllConditions.+1)))        
         plot!(thisPlotStd,xticks=(collect(0:hoursToPlot*60/4:hoursToPlot*60),collect(0:hoursToPlot./4:hoursToPlot)),ylim=(0,maxValOfYAxis),xlim=(0,hoursToPlot*60),dpi=300,size=(750,500),xtickfontsize=18,ytickfontsize=18)
#        plot!(thisPlotStd,xticks=(collect(0:hoursToPlot*60/4:hoursToPlot*60),collect(0:hoursToPlot./4:hoursToPlot)),xlim=(0,hoursToPlot*60),dpi=300,size=(750,500),xtickfontsize=18,ytickfontsize=18)
        #display(plot(boxPlotAll,thisPlot))
        display(plot(boxPlotAll,thisPlotStd,layout = grid(1, 2, widths=[0.4 ,0.6])))
    end
end


plotAllSpecies (generic function with 1 method)

First we'll run the WT condition with with IKK inputs, followed by repeating the simulations with 10X RelA synthesis and 10x cRel synthesis. We specify and output folder so that the next simulations we run can go to a different folder.

In [10]:
#conditions=["WT","moreRelA","morecRel","moreRelB","morep100","moreRelBAndp100","morep50"]
conditions=["WT","moreRelA","morecRel","moreRelB"]
#paramsToChange=[["k1_RelASynth"],["k1_RelASynth","k1_cRelSynth"],["k1_RelASynth","k1_cRelSynth"],["basal_RelBSynth"],["basal_p100Synth"],["basal_RelBSynth","basal_p100Synth"],["basal_p50Synth"]]
paramsToChange=[["k1_RelASynth"],["k1_RelASynth","basal_cRelSynth"],["k1_RelASynth","basal_cRelSynth"],["k1_RelASynth","basal_RelBSynth"]]
# modifyAmount=[
#         [1.0],[10,1.0],[1.0,10],[10],[10],[10,10],[10]
#     ]
modifyAmount=[
         [1.0],[10,1.0],[1.0,10],[1.0,10]
     ]
IKKSSArray=[ikkSS,ikkSS,ikkSS,ikkSS]
IKKTCArray=[ikkTC,ikkTC,ikkTC,ikkTC]
NIKSSArray=[NIKFuncSS,NIKFuncSS,NIKFuncSS,NIKFuncSS]
NIKTCArray=[NIKFuncSS,NIKFuncSS,NIKFuncSS,NIKFuncSS]
println("Summary of conditions being run:")
folder="outputsWithRelB"
show(IOContext(stdout, :limit => false), "text/plain", hcat(conditions,paramsToChange,modifyAmount))


Summary of conditions being run:
4×3 Matrix{Any}:
 "WT"        ["k1_RelASynth"]                     [1.0]
 "moreRelA"  ["k1_RelASynth", "basal_cRelSynth"]  [10.0, 1.0]
 "morecRel"  ["k1_RelASynth", "basal_cRelSynth"]  [1.0, 10.0]
 "moreRelB"  ["k1_RelASynth", "basal_RelBSynth"]  [1.0, 10.0]

In [ ]:
runSimulationNew(first_cell,last_cell,conditions,folder,IKKSSArray,IKKTCArray,NIKSSArray,NIKTCArray)

To plot the outputs just specify which folder you want to plot and then which conditions and species you want to plot.

# Figure 1C

In [12]:
###### folder="outputs"
hoursToPlot=2
colorArray=palette(:seaborn_colorblind)
folder="outputsWithRelB"
#conditions=["WT","moreRelA","morecRel","moreRelB","morep100","moreRelBAndp100","morep50"]
conditions=["WT","moreRelA","morecRel","moreRelB"]
speciesToPlot=["cRelnp50n","RelAnp50n"]
maxValOfYAxis=55
plotly()
plotAllSpecies(speciesToPlot,conditions,colorArray,first_cell,last_cell,folder,hoursToPlot,maxValOfYAxis)